In [19]:
import netgen.gui
from ngsolve import *
from netgen.csg import *
from math import pi
from netgen.geom2d import unit_square

mesh = Mesh(unit_square.GenerateMesh(maxh=0.5))

#exact u
u1=sin(pi*x)*sin(pi*y)
u2=cos(pi*x)*cos(pi*y)
uexact = CoefficientFunction((u1, u2))
#exact p
pexact = CoefficientFunction(sin(pi*x)*cos(pi*y))
#source f
f1=2*(pi**2)*sin(pi*x)*sin(pi*y)+pi*cos(pi*x)*cos(pi*y)
f2=2*(pi**2)*cos(pi*x)*cos(pi*y)-pi*sin(pi*x)*sin(pi*y)
source=CoefficientFunction((f1,f2))

k = 2
V = VectorH1(mesh,order=k)
Q = H1(mesh,order=k-1)
R = NumberSpace(mesh) 
X = FESpace([V, Q, R, R])
#X = FESpace([V,Q])

gfu = GridFunction(X)

(u,p, lam1, lam2), (v,q, mu1, mu2) = X.TnT()
#(u,p), (v,q) = X.TnT() 
lam = CoefficientFunction((lam1, lam2))
mu = CoefficientFunction((mu1, mu2))

n = specialcf.normal(mesh.dim)

graduexact = CoefficientFunction((pi*cos(pi*x)*sin(pi*y), pi*sin(pi*x)*cos(pi*y), \
        -pi*sin(pi*x)*cos(pi*y), -pi*cos(pi*x)*sin(pi*y)), dims=(2,2))

I = CoefficientFunction((1, 0, 0, 1), dims=(2,2))
g= (-graduexact + pexact * I)

a = BilinearForm(X)
a += (InnerProduct(grad(u),grad(v))-div(v)*p-div(u)*q)*dx
a += (lam*v+mu*u) * dx 

f = LinearForm(X)
f += source*v*dx
f += - InnerProduct(g*n,v)*ds(definedon=mesh.Boundaries("top|bottom|left|right"))

a.Assemble()
f.Assemble()

inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
res = f.vec.CreateVector()
res.data = f.vec - a.mat*gfu.vec
gfu.vec.data += inv * res

#Solve Stokes function
gfu = GridFunction(X)

output = []
def SolveStokes():
    X.Update()
    gfu.Update()

    #Linear forms
    a.Assemble()
    f.Assemble()

    # Solve
    inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
    res = f.vec.CreateVector()
    res.data = f.vec - a.mat*gfu.vec
    gfu.vec.data += inv * res

    velocity = gfu.components[0]
    Draw(velocity,mesh,"u")
    pressure = gfu.components[1]
    Draw(pressure,mesh,"p")

    #error
    u=gfu.components[0]
    p=gfu.components[1]
    err_u =  sqrt (Integrate ((u-uexact)**2, mesh))
    err_p =  sqrt (Integrate ((p-pexact)**2, mesh))
    output.append ((X.ndof, err_u,err_p))
    print(output)

while X.ndof < 15000:
    mesh.Refine()
    SolveStokes()
#Make a table of convergence
i = 1
while i < len(output):
    order_u = log(output[i-1][1]/output[i][1])/log(2)
    order_p = log(output[i-1][2]/output[i][2])/log(2)
    #print order_u, error_u, order_p, error_p
    print("%0.3f | %0.3e || %0.3f | %0.3e " %
      (order_u, output[i-1][1], order_p, output[i-1][2]))
    i =  i+1


[(153, 0.40540903759306546, 0.05522090514395135)]
[(153, 0.40540903759306546, 0.05522090514395135), (517, 0.40528706355917177, 0.01107865267172447)]
[(153, 0.40540903759306546, 0.05522090514395135), (517, 0.40528706355917177, 0.01107865267172447), (1893, 0.40528477471569, 0.0026053255999712926)]
[(153, 0.40540903759306546, 0.05522090514395135), (517, 0.40528706355917177, 0.01107865267172447), (1893, 0.40528477471569, 0.0026053255999712926), (7237, 0.4052847352193775, 0.0006362286766100719)]
[(153, 0.40540903759306546, 0.05522090514395135), (517, 0.40528706355917177, 0.01107865267172447), (1893, 0.40528477471569, 0.0026053255999712926), (7237, 0.4052847352193775, 0.0006362286766100719), (28293, 0.405284734579642, 0.00015729243667874003)]
0.000 | 4.054e-01 || 2.317 | 5.522e-02 
0.000 | 4.053e-01 || 2.088 | 1.108e-02 
0.000 | 4.053e-01 || 2.034 | 2.605e-03 
0.000 | 4.053e-01 || 2.016 | 6.362e-04 


In [ ]:
[(153, 0.40540903759306546, 0.05522090514395135), (517, 0.40528706355917177, 0.01107865267172447), (1893, 0.40528477471569, 0.0026053255999712926), (7237, 0.4052847352193775, 0.0006362286766100719), (28293, 0.405284734579642, 0.00015729243667874003)]
0.000 | 4.054e-01 || 2.317 | 5.522e-02 
0.000 | 4.053e-01 || 2.088 | 1.108e-02 
0.000 | 4.053e-01 || 2.034 | 2.605e-03 
0.000 | 4.053e-01 || 2.016 | 6.362e-04